In [7]:
import nltk, os, collections, csv, re
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords
from pywsd.utils import lemmatize, lemmatize_sentence

from gensim.models import Phrases
from gensim.models.word2vec import LineSentence

import spacy, codecs, re, os
import pandas as pd

nlp = spacy.load('en')

#list of all contractions to reorganize texts
cList = {
"ain't": "am not",
"aren't": "are not",
"can't": "cannot",
"can't've": "cannot have",
"'cause": "because",
"could've": "could have",
"couldn't": "could not",
"couldn't've": "could not have",
"didn't": "did not",
"doesn't": "does not",
"don't": "do not",
"hadn't": "had not",
"hadn't've": "had not have",
"hasn't": "has not",
"haven't": "have not",
"he'd": "he would",
"he'd've": "he would have",
"he'll": "he will",
"he'll've": "he will have",
"he's": "he is",
"how'd": "how did",
"how'd'y": "how do you",
"how'll": "how will",
"how's": "how is",
"I'd": "I would",
"I'd've": "I would have",
"I'll": "I will",
"I'll've": "I will have",
"I'm": "I am",
"I've": "I have",
"isn't": "is not",
"it'd": "it had",
"it'd've": "it would have",
"it'll": "it will",
"it'll've": "it will have",
"it's": "it is",
"let's": "let us",
"ma'am": "madam",
"mayn't": "may not",
"might've": "might have",
"mightn't": "might not",
"mightn't've": "might not have",
"must've": "must have",
"mustn't": "must not",
"mustn't've": "must not have",
"needn't": "need not",
"needn't've": "need not have",
"o'clock": "of the clock",
"oughtn't": "ought not",
"oughtn't've": "ought not have",
"shan't": "shall not",
"sha'n't": "shall not",
"shan't've": "shall not have",
"she'd": "she would",
"she'd've": "she would have",
"she'll": "she will",
"she'll've": "she will have",
"she's": "she is",
"should've": "should have",
"shouldn't": "should not",
"shouldn't've": "should not have",
"so've": "so have",
"so's": "so is",
"that'd": "that would",
"that'd've": "that would have",
"that's": "that is",
"there'd": "there had",
"there'd've": "there would have",
"there's": "there is",
"they'd": "they would",
"they'd've": "they would have",
"they'll": "they will",
"they'll've": "they will have",
"they're": "they are",
"they've": "they have",
"to've": "to have",
"wasn't": "was not",
"we'd": "we had",
"we'd've": "we would have",
"we'll": "we will",
"we'll've": "we will have",
"we're": "we are",
"we've": "we have",
"weren't": "were not",
"what'll": "what will",
"what'll've": "what will have",
"what're": "what are",
"what's": "what is",
"what've": "what have",
"when's": "when is",
"when've": "when have",
"where'd": "where did",
"where's": "where is",
"where've": "where have",
"who'll": "who will",
"who'll've": "who will have",
"who's": "who is",
"who've": "who have",
"why's": "why is",
"why've": "why have",
"will've": "will have",
"won't": "will not",
"won't've": "will not have",
"would've": "would have",
"wouldn't": "would not",
"wouldn't've": "would not have",
"y'all": "you all",
"y'alls": "you alls",
"y'all'd": "you all would",
"y'all'd've": "you all would have",
"y'all're": "you all are",
"y'all've": "you all have",
"you'd": "you had",
"you'd've": "you would have",
"you'll": "you you will",
"you'll've": "you you will have",
"you're": "you are",
"you've": "you have"
}

c_re = re.compile('(%s)' % '|'.join(cList.keys()))

#Preprocessing of texts: removing sentiment adjectives, lowercase, expand contractions, tokenization

def lemmatized_sentence_corpus(filename):
    def expandContractions(text, c_re=c_re):
        def replace(match):
            return cList[match.group(0)]
        return c_re.sub(replace, text)

    def punct_space(token):
        return token.is_punct or token.is_space

    neg_path = ('om_lexicon//negative-words.txt')
    pos_path = ('om_lexicon//positive-words.txt')
    with open(neg_path) as f:
        neg_list = ([line[:-1] for line in open(neg_path)])
    with open(pos_path) as f:
        pos_list = ([line[:-1] for line in open(pos_path)])
    sentiments = pos_list+neg_list
#     print (sentiments)
        
    with codecs.open(filename, encoding='utf-8') as f:
        i = 0
        for line in f:
            review = line.split('; ')[5]
            i+=1
            if i%1000 == 0:
                print ('count: ', i)
            review = review.split()
#             print (review)
            review = [r for r in review if r.lower() not in sentiments]
            review = ' '.join([el for el in review])
            parsed_review = nlp(expandContractions(review.replace('\\n', '\n')))
            item = line.split('; ')[0]
            id = line.split('; ')[2]
            votes = line.split('; ')[3]
            rating = line.split('; ')[4]
#             print (review)
            for sent in parsed_review.sents:
                yield ' '.join([token.lemma_ for token in sent
                                 if not punct_space(token) and len(token)>1])

In [8]:
# if lines with reviews and other information were parsed badly

# with open('C:\\Users\\liliya.akhtyamova\\Documents\\reviews\\full_reviews\\pwr\\36rrc4k3\\rawdata\\full_data_electronics.txt') as f, open('C:\\Users\\liliya.akhtyamova\\Documents\\reviews\\full_reviews\\pwr\\36rrc4k3\\rawdata\\data_electronics_partial1.txt', 'a') as fout2:
#     i = 0

#     for line in f:
#         try:
#             review = line.split('; ')[5]
#             fout2.write(line)
#             i+=1
#         except:
#             pass
#         if i%50 == 0:
#             print (i)

In [9]:
intermediate_directory = 'reviews_tv'
review_txt_filepath = os.path.join(intermediate_directory,
                                   'data_tv_partial.txt')
unigram_sentences_filepath = os.path.join(intermediate_directory,
                                          'unigram_sentences_all_tv.txt')

In [10]:
# Creating bigrams

with codecs.open(unigram_sentences_filepath, 'w', encoding='utf-8') as f:
        for sentence in lemmatized_sentence_corpus(review_txt_filepath):
            f.write(sentence + '\n')
#             print (sentence)

unigram_sentences = LineSentence(unigram_sentences_filepath)

bigram_model_filepath = os.path.join(intermediate_directory, 'bigram_model_all3')
# print (reviews)
bigram_model = Phrases(unigram_sentences)

bigram_model.save(bigram_model_filepath)

# load the finished model from disk
bigram_model = Phrases.load(bigram_model_filepath)

bigram_sentences_filepath = os.path.join(intermediate_directory,
                                         'bigram_sentences_all_tv.txt')
with codecs.open(bigram_sentences_filepath, 'w', encoding='utf-8') as f:
    for unigram_sentence in unigram_sentences:
        bigram_sentence = ' '.join(bigram_model[unigram_sentence])
        f.write(bigram_sentence + '\n')
            
bigram_sentences = LineSentence(bigram_sentences_filepath)

count:  1000
count:  2000
count:  3000
count:  4000
count:  5000
count:  6000
count:  7000
count:  8000
count:  9000
count:  10000
count:  11000
count:  12000
count:  13000
count:  14000
count:  15000
count:  16000
count:  17000
count:  18000
count:  19000
count:  20000
count:  21000
count:  22000
count:  23000
count:  24000
count:  25000
count:  26000
count:  27000
count:  28000
count:  29000
count:  30000
count:  31000
count:  32000
count:  33000
count:  34000
count:  35000
count:  36000


C:\Users\liliya.akhtyamova\Anaconda3\lib\site-packages\gensim\models\phrases.py:274: UserWarning: For a faster implementation, use the gensim.models.phrases.Phraser class
  warnings.warn("For a faster implementation, use the gensim.models.phrases.Phraser class")


In [11]:
import itertools as it

trigram_model_filepath = os.path.join(intermediate_directory,
                                      'trigram_model_all3')
trigram_model = Phrases(bigram_sentences)

trigram_model.save(trigram_model_filepath)
    
# load the finished model from disk
trigram_model = Phrases.load(trigram_model_filepath)

trigram_sentences_filepath = os.path.join(intermediate_directory,
                                          'trigram_sentences_tv.txt')

with codecs.open(trigram_sentences_filepath, 'w', encoding='utf_8') as f:
        for bigram_sentence in bigram_sentences:
                trigram_sentence = ' '.join(trigram_model[bigram_sentence])
                f.write(trigram_sentence + '\n')
        
trigram_sentences = LineSentence(trigram_sentences_filepath)

C:\Users\liliya.akhtyamova\Anaconda3\lib\site-packages\gensim\models\phrases.py:274: UserWarning: For a faster implementation, use the gensim.models.phrases.Phraser class
  warnings.warn("For a faster implementation, use the gensim.models.phrases.Phraser class")


# *The trigram model per each sentence was created (see: http://nbviewer.jupyter.org/github/skipgram/modern-nlp-in-python/blob/master/executable/Modern_NLP_in_Python.ipynb#topic=0&lambda=1&term=). Now it's a time to transform each review using built trigram model*

In [12]:
import nltk, os, collections, csv, re
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords
from pywsd.utils import lemmatize, lemmatize_sentence

from gensim.models import Phrases
from gensim.models.word2vec import LineSentence

import spacy, codecs, re, string
import pandas as pd

import os, codecs
import unicodedata
import sys
nlp = spacy.load('en')

# intermediate_directory = 'reviews_tv'
# review_txt_filepath = os.path.join(intermediate_directory,
#                                    'data_tv_partial.txt')

# cList = {
# "ain't": "am not",
# "aren't": "are not",
# "can't": "cannot",
# "can't've": "cannot have",
# "'cause": "because",
# "could've": "could have",
# "couldn't": "could not",
# "couldn't've": "could not have",
# "didn't": "did not",
# "doesn't": "does not",
# "don't": "do not",
# "hadn't": "had not",
# "hadn't've": "had not have",
# "hasn't": "has not",
# "haven't": "have not",
# "he'd": "he would",
# "he'd've": "he would have",
# "he'll": "he will",
# "he'll've": "he will have",
# "he's": "he is",
# "how'd": "how did",
# "how'd'y": "how do you",
# "how'll": "how will",
# "how's": "how is",
# "I'd": "I would",
# "I'd've": "I would have",
# "I'll": "I will",
# "I'll've": "I will have",
# "I'm": "I am",
# "I've": "I have",
# "isn't": "is not",
# "it'd": "it had",
# "it'd've": "it would have",
# "it'll": "it will",
# "it'll've": "it will have",
# "it's": "it is",
# "let's": "let us",
# "ma'am": "madam",
# "mayn't": "may not",
# "might've": "might have",
# "mightn't": "might not",
# "mightn't've": "might not have",
# "must've": "must have",
# "mustn't": "must not",
# "mustn't've": "must not have",
# "needn't": "need not",
# "needn't've": "need not have",
# "o'clock": "of the clock",
# "oughtn't": "ought not",
# "oughtn't've": "ought not have",
# "shan't": "shall not",
# "sha'n't": "shall not",
# "shan't've": "shall not have",
# "she'd": "she would",
# "she'd've": "she would have",
# "she'll": "she will",
# "she'll've": "she will have",
# "she's": "she is",
# "should've": "should have",
# "shouldn't": "should not",
# "shouldn't've": "should not have",
# "so've": "so have",
# "so's": "so is",
# "that'd": "that would",
# "that'd've": "that would have",
# "that's": "that is",
# "there'd": "there had",
# "there'd've": "there would have",
# "there's": "there is",
# "they'd": "they would",
# "they'd've": "they would have",
# "they'll": "they will",
# "they'll've": "they will have",
# "they're": "they are",
# "they've": "they have",
# "to've": "to have",
# "wasn't": "was not",
# "we'd": "we had",
# "we'd've": "we would have",
# "we'll": "we will",
# "we'll've": "we will have",
# "we're": "we are",
# "we've": "we have",
# "weren't": "were not",
# "what'll": "what will",
# "what'll've": "what will have",
# "what're": "what are",
# "what's": "what is",
# "what've": "what have",
# "when's": "when is",
# "when've": "when have",
# "where'd": "where did",
# "where's": "where is",
# "where've": "where have",
# "who'll": "who will",
# "who'll've": "who will have",
# "who's": "who is",
# "who've": "who have",
# "why's": "why is",
# "why've": "why have",
# "will've": "will have",
# "won't": "will not",
# "won't've": "will not have",
# "would've": "would have",
# "wouldn't": "would not",
# "wouldn't've": "would not have",
# "y'all": "you all",
# "y'alls": "you alls",
# "y'all'd": "you all would",
# "y'all'd've": "you all would have",
# "y'all're": "you all are",
# "y'all've": "you all have",
# "you'd": "you had",
# "you'd've": "you would have",
# "you'll": "you you will",
# "you'll've": "you you will have",
# "you're": "you are",
# "you've": "you have"
# }

# c_re = re.compile('(%s)' % '|'.join(cList.keys()))

tbl = dict.fromkeys(i for i in range(sys.maxunicode)
                      if unicodedata.category(chr(i)).startswith('P'))

In [17]:
def remove_punctuation(text):
    return text.translate(tbl)

neg_path = ('om_lexicon//negative-words.txt')
pos_path = ('om_lexicon//positive-words.txt')
with open(neg_path) as f:
    neg_list = ([line[:-1] for line in open(neg_path)])
with open(pos_path) as f:
    pos_list = ([line[:-1] for line in open(pos_path)])
sentiments = pos_list+neg_list

def expandContractions(text, c_re=c_re):
        def replace(match):
            return cList[match.group(0)]
        return c_re.sub(replace, text)
    
def punct_space(token):
        return token.is_punct or token.is_space
    
def line_review(filename):
    """
    generator function to read in reviews from the file
    and un-escape the original line breaks in the text
    """
    
    with codecs.open(filename, encoding='utf-8') as f:
        for line in f:
            try:
                review = expandContractions(line.split('; ')[5])
                review = review.split()
    #             print (review)
                review = [r for r in review if remove_punctuation(r) not in sentiments]
                review = ' '.join([el for el in review])
                yield review.replace('\\n', '\n')
#                 fout2.write(line)
            except:
                pass
        f.close()

trigram_reviews_filepath = os.path.join(intermediate_directory,
                                        'trigram_transformed_reviews_tvs.txt')

neg_path = ('negative-words.txt')
pos_path = ('positive-words.txt')



with codecs.open(trigram_reviews_filepath, 'w', encoding='utf-8') as f:
        
    for parsed_review in nlp.pipe(line_review(review_txt_filepath),
                                  batch_size=10000, n_threads=4):

        # lemmatize the text, removing punctuation and whitespace
        unigram_review = [token.lemma_ for token in parsed_review
                          if not punct_space(token)]
        # apply the first-order and second-order phrase models
        bigram_review = bigram_model[unigram_review]
        trigram_review = trigram_model[bigram_review]

        # remove any remaining stopwords
        trigram_review = [term for term in trigram_review
                          if term not in spacy.en.language_data.STOP_WORDS]

        # write the transformed review as a line in the new file
        trigram_review = ' '.join(trigram_review)
#         print (trigram_review)
        f.write(trigram_review + '\n')
    f.close()

C:\Users\liliya.akhtyamova\Anaconda3\lib\site-packages\gensim\models\phrases.py:274: UserWarning: For a faster implementation, use the gensim.models.phrases.Phraser class
  warnings.warn("For a faster implementation, use the gensim.models.phrases.Phraser class")


In [ ]:
# partial1 = open('C:\\Users\\liliya.akhtyamova\\Documents\\reviews\\full_reviews\\pwr\\36rrc4k3\\rawdata\\data_electronics_partial1.txt')

with open('reviews_tv//trigram_transformed_reviews_tvs.txt') as rev, open(review_txt_filepath) as others:
    for reviews_line, others_line in zip(rev, others):
#       print (others_line.strip())
        skus = others_line.split('; ')[0]
        descr = others_line.split('; ')[1]
        id_review = others_line.split('; ')[2]
        votes = others_line.split('; ')[3]
#         print (votes)
        rating = others_line.split('; ')[4]
        initial_review = others_line.split('; ')[5]
        words = collections.Counter()
        tokens = reviews_line.split()
        print (tokens)
        tokens = [r for r in tokens if (r not in sentiments and r != '-PRON-')]
#         print (tokens)

        for token in tokens:
            if len(token) > 2:
                token = token.lower()
                if len(token) > 0:
                    words[token] += 1
       
                
        def construct_bow(words):
        
            stop_words = set(stopwords.words('english'))
            return [
            (
            word.replace(' ', '_').replace(':', '_').replace('|', '_').replace('\t', '_') + 
            ('' if cnt == 1 else ':%g' % cnt)
            )
            for word, cnt in words.items() if not word in stop_words
            ]
        
        if len(words) > 3:
            parts = (
            ['%d' % int(id_review)] + 
            ['|@words'] + construct_bow(words) +
            #         ['|@headline'] + construct_bow({headlines: 1 for headlines in headline}) +
            ['|@sku %s' % str(skus)] +
            ['|@votes %d' % int(votes)] +
            ['|@metrics %d' % int(rating)] 
            )  
            line = ' '.join(parts)

            with open('wv_tvs.txt', 'a') as fout, open('data_tv_for_wv.txt', 'a') as fout2:
                    fout.write(line + "\n")
                    fout2.write('; '.join([skus, descr, id_review, votes, rating, initial_review]))

['product', 'consider', 'buy', 'brand', 'tv']
['use', '-PRON-', 'bedroom', 'product', 'jack', 'ear', 'bud', 'listen', 'private', 'partner', 'unfortunately', 'product', 'meet', '-PRON-', 'need', 'return', 'dealer']
['great', 'little', 'tv', 'color', 'sound', 'set', 'use']
['overall', 'tv', 'adjustment', '-PRON-', '-PRON-', '-PRON-', 'slight', 'difference', 'color', 'temperature', 'half', 'screen', 'left', 'half', 'right', 'slightly', 'greenish', 'left', 'slightly', 'easy', 'gray', 'scale', 'screen', '-PRON-', 'know', 'look', '-PRON-', 'bet', 'people', 'notice', 'screen', 'type', 'notification', 'pedestrian', '-PRON-', 'look', 'at_least', 'effect', 'basic', 'quality', 'image', 'aside_from', 'left', 'right', 'shift', 'audio', '-PRON-', '-PRON-', 'find', 'compel', 'fiddle', '-PRON-', 'compare', 'set', '-PRON-', 'tv', 'price']
['-PRON-', 'purchase', 'tv', '-PRON-', 'space', 'camper', 'tv', 'far', '-PRON-', 'tv', '-PRON-', 'replace', 'old', '15', 'non', 'digital', 'tv', 'special', 'digital',

['seven', 'day', 'sound', 'tv', 'turn_off', 'pull', 'power_cord', 'return', '-PRON-', 'walmart']
['big', 'piece', '-PRON-', 'buy', 'stay_away']
['-PRON-', '-PRON-', 'purchase', '-PRON-', 'wait', 'delivery', '-PRON-', '3d', 'tv', '-PRON-', 'store', 'express', '-PRON-', 'salesman', '-PRON-', 'certainly', 'switch', '3d', 'model', '-PRON-', 'cost', '-PRON-', 'tv', '-PRON-', 'purchase', 'picture', '-PRON-', 'know', 'difference', 'guess', '-PRON-', '100%', '-PRON-', 'new', 'hd', 'tv', "'s", '3d', '-PRON-', 'come', 'close', 'quality', 'picture', 'tv', '-PRON-', 'believe', 'samsung', "'s", 'new', 'suhdtv', '4', 'k', 'un78js9100fxza', 'tv', 'course', 'thing', 'change', '-PRON-']
['screen', 'voice', 'fantastic.i', 'watch', 'movie', 'home']
['feature', 'tv', 'deliver', 'excellent', 'sound', 'smartness', 'bit', '-PRON-', 'removal', 'certain', 'functionality', 'late', 'update', '-PRON-', 'purchase', 'tv', 'week', 'december_2015', 'follow', 'week', 'update', 'late', 'update', 'remove', 'guide', 'dvr

['set', 'immediately_understand_why', 'expert_reviewer_compare', '-PRON-', 'tv', 'cost_thousand_more', 'plenty', 'technology', 'tech_spec', 'tell', 'whole_story', 'lot', 'picture', 'software', 'processing', 'lg', 'end', 'result', 'picture', 'color', 'saturate', 'skin_tone', 'truly', 'context', '-PRON-', 'pull', 'set', '-PRON-', '-PRON-', 'design', 'black', 'plastic', 'set', 'look', '-PRON-', 'remote', 'control', 'simple', 'use', 'especially', '-PRON-', 'let', '-PRON-', 'control', 'device', '-PRON-', 'cable_box', '-PRON-', 'find', '-PRON-', 'able', 'customize', 'smart', 'tv', 'interface', '-PRON-', 'big', 'deal', '-PRON-', 'hop', 'lg', 'address', 'software_update', 'tv', 'update', '-PRON-', '-PRON-', '-PRON-', '-PRON-', 'functionality', 'continue', 'add', 'main', 'thing', 'picture', 'quality', '-PRON-', 'day', 'live', 'set', '-PRON-']
['picture', 'led', 'feature', '-PRON-', 'youtube', 'netflix', 'remote', 'pointer', 'include', 'phone', 'app', 'point&click', 'mouse', 'design', 'slim', '-

['-PRON-', 'buy', 'tv', '24_hour', 'ago', '60hz_rate', 'sport', 'viewing', 'demand', 'movie', 'stream', '-PRON-', 'notice_jumps', 'object_person', 'screen', 'power', 'sound', '-PRON-', 'read', 'tv', 'build', 'surround_sound', 'bass', 'tv', '-PRON-', '-PRON-', 'volume', 'demand', 'streaming', 'live', 'tv', 'bass', 'surround_sound', 'feature', 'lg', 'list', '-PRON-', 'tv', '120hz', 'state', '-PRON-', 'tru_motion_120', 'acual_120hz', 'think', '-PRON-', 'hz', '120', '-PRON-', 'return', 'tv', '-PRON-', 'look', 'tv', 'jumping', 'viewing', 'lack_lustre', 'sound', 'quality', 'deal_breaker']
['tv', '-PRON-', 'buy', '8', 'year', '-PRON-', 'family_room', '-PRON-', 'tv', '42_plasma', '-PRON-', '-PRON-', 'bedroom', 'look', 'new', 'tv', 'plasma', 'tv', 'start', '-PRON-', 'set', 'tv', 'hour', 'tweak', 'video', 'sound', 'setting', 'hdmi_input', 'tv', 'look', 'sound', 'amazing', 'tech_guy_who', 'particular', 'audio', 'video', '-PRON-', 'tv']
['-PRON-', 'smart', 'tv', '-PRON-', 'happen', '4', 'k', 'love

['-PRON-', 'buy', 'tv', 'yesterday', '-PRON-', '-PRON-', '-PRON-', 'screen', '-PRON-', 'feel', '-PRON-', 'actually', 'movie', '-PRON-', 'need', 'movie']
['stream', 'netflix', '-PRON-', 'reprogram', '-PRON-', 'tv', 'netflix', 'stream', 'real', '-PRON-', 'know', '-PRON-', 'tv', '-PRON-', 'tvs', 'home', 'hulu', 'alot', '-PRON-', '-PRON-', 'play', 'tv', "'s", 'electronic', '-PRON-', 'lg', '4k', 'tv']
['-PRON-', 'buy', 'tv', 'month_ago', '-PRON-', '-PRON-', 'able', 'relabel', '-PRON-', 'input', '-PRON-', '-PRON-', 'tv', "'s"]
['picture', 'scale', 'feature', 'difference', 'picture', 'hd', 'easy', 'set', 'use']
['-PRON-', 'buy', 'tv', 'tax_return', '6', 'week_ago', '-PRON-', 'size', 'picture', 'quality', '-PRON-', 'use', 'hdmi1_port', 's', 'manual', 'use', 'uhd', '-PRON-', 'family', '-PRON-', 'logger', 'sign', '-PRON-', 'xbox', '-PRON-', 'netflix', 'amazon_prime_account', '-PRON-', 'tell', '-PRON-', '-PRON-', 'thing', 'tv', '-PRON-', 'youtube', 'lol']
['tv', '3', 'month', 'crystal', 'quality'

...

['-PRON-', '-PRON-', 'hook_up', 'process', '-PRON-', 'setup', '-PRON-', 'liking', 'use', 'flat_screen', 'tv', '-PRON-', 'picture', 'different', 'crt', 'tv', 'book', 'come', '-PRON-', 'actually', 'page', 'instead', 'fold', 'sheet', 'writing', 'small', 'read', '-PRON-', '-PRON-', 'find', 'manual', 'line', 'booklet', 'form', 'come', 'tv', '-PRON-', 'come', 'shop', 'mode', 'home', 'mode', '-PRON-', 'realize', 'till', 'couple', 'day', 'later', 'figure_out', '-PRON-', 'change', '-PRON-', 'preset_setting', '-PRON-', 'set', '-PRON-', 'default', '-PRON-', 'watch', 'lot', 'air_station', 'far', '-PRON-', 'find', 'save', '-PRON-', 'find', '-PRON-', 'scan', 'channel', 'station', 'different', 'direction', '-PRON-', 'set', 'check', 'channel', 'thing', '-PRON-', 'let', '-PRON-', 'save', '-PRON-', 'find', 'search', 'station', 'find', '-PRON-', '-PRON-', 'add', '-PRON-', '-PRON-', 'find', 'list', '-PRON-', 'hope', 'option', 'far', 'turn', 'sound', 'lot', '-PRON-', 'dvd', 'play', 'channel', '4', 'satelli

['-PRON-', 'buy', '24_inch', 'led', 'tv', '-PRON-', 'mother', 'christmas_gift', '-PRON-', 'use', '-PRON-', '-PRON-', 'dining_room', '-PRON-', 'watch', '-PRON-', 'program', 'eat', '-PRON-', 'meal', '-PRON-', 'small', 'fit', 'space', 'screen', 'large', '-PRON-', 'view', '-PRON-', 'program', '-PRON-', 'ill', 'fat', 'eye', '-PRON-', 'cable', 'service', '-PRON-', 'connect', 'mohu', '30', 'antenna', 'use', 'coax', 'connector', 'rear', 'console', 'use', 'air', 'feature', 'setting', '-PRON-', 'able', 'acquire', 'local', 'digital', 'hd', 'channel', 'viewing', 'area', 'station', '30', 'mile', 'radius', '-PRON-', 'location', 'result', '-PRON-', 'plenty', 'channel', 'watch', 'need', 'picture', 'adjustment', 'picture', 'quality', 'box', 'sound', 'quality', 'button', 'remote', 'control', 'large', 'lettering', 'button', '-PRON-', 'use', '-PRON-', 'assistance', 'magnifying', 'glass', 'samsung', 'ledtv', 'tv', '-PRON-', '-PRON-', '-PRON-', '-PRON-', '-PRON-', 'buy', '32_inch', 'model', '-PRON-', 'bedro

['tv', 'picture', '-PRON-', 'cable', 'system', 'prefer', 'pedestal_stand', 'middle', 'instead', '4', 'leg', 'allow', '-PRON-', 'fit', '-PRON-', 'sit', 'sound', 'quality', '-PRON-', 'system', 'like', 'flat', 'monitor', 'instead', 'boxy', 'type', '-PRON-', 'tv']
['ideal', 'tv', 'bedroom', 'easy', 'connect', 'excellent', 'picture', 'sound', 'onscreen', 'programming', 'navigate']
['perfect', 'size', 'bedroom', 'great', 'quality', '-PRON-', '46', 'samsung', 'living_room', '-PRON-', '-PRON-', 'decide', 'stick', 'brand']
['samsung', 'device', '-PRON-', 'family', '30', 'year', 'company', 'service', 'anybody', '5', 'star', '-PRON-']
['-PRON-', 'ne', 'small', 'tv', '-PRON-', 'office', '-PRON-', 'pick', 'samsung', '-PRON-', 'feature', '-PRON-', 'ne', 'price']
['bought', 'extra', 'bedroom', '-PRON-', 'size', 'feature', 'guest']
['tv', 'sum', '-PRON-', 'kind', '-PRON-', '-PRON-', 'ear', 'phone', 'jack', 'easily', 'fix', 'buy', 'optical', '3.5', 'mm', 'female', 'mini', 'jack', 'plug', 'digital', 'to

['order', '-PRON-', 'online', 'store', 'pickup', 'lay', 'away', 'area', 'navigate', 'staff', 'tv', '-PRON-', 'addition', '-PRON-', 'guest', 'suite']
['-PRON-', 'mom', 'samsung', '24', 'sound', 'volume', 'exchange', 'television', 'samsung', '24']
['tv', 'unit', 'control', 'volume', 'channel', 'selection', 'remote', 'tv', 'unit', 'headphone_jack', 'provide', 'component', 'video', 'connection', 'function', 'connect', 'dvd_player', 'use', 'composite', 'video', 'connection', 'instead', 'plan', 'return', 'tv', 'walmart', 'deficience']
['-PRON-', 'read', 'review', 'sound', 'quality', 'tv', '-PRON-', 'assume', 'saying', 'choosy', '-PRON-', 'sound', 'decide', 'try', '-PRON-', 'anyways', 'turn', 'way', '-PRON-', 'barely', 'understand', 'conversation', '-PRON-', 'couch', 'picture', '-PRON-', 'external_speaker', '-PRON-', '-PRON-', '-PRON-', 'sense', 'tv', '-PRON-', 'return', '-PRON-']
['tv', '-PRON-', 'picture', '-PRON-', 'buy', 'idea', 'pc_monitor', '-PRON-', 'hookup', 'monitor', 'pc', '-PRON-',

['television', 'ok', 'sound', 'minimal', 'picture', 'quality', '-PRON-', 'sit_directly', 'face', 'screen', 'color', 'appear', 'fade', 'slight', 'position', 'view', '-PRON-', 'want', 'sanyo', 'settle', 'samsung', 'lesson_learn']
['sound', 'picture', 'fit', 'small', 'apt']
['picture', 'sound', 'set', '-PRON-', '-PRON-', '-PRON-', 'woman', '80', 'love', '-PRON-', 'perfect', 'size', '-PRON-', 'corner', 'kitchen']
['purchase', 'tv', 'bedroom', 'picture', 'quality', 'tweak', 'sound', 'control', 'tv', '-PRON-', 'remote', '-PRON-', 'big', 'let', 'tv', 'micro_hdmi', 'hdmi', 'try', 'hook_up', 'nokia', 'lumia', '2520', 'tablet', 'use', 'micro_hdmi', 'picture', 'sound', 'tv', 'contact', 'sumsung', '-PRON-', 'blame', 'tablet', '-PRON-', 'use', 'tablet', 'micro_hdmi', '-PRON-', 'tv', "'s", 'ended', '-PRON-', 'purchase', 'toshiba', '32l1400', 'far', 'quality', 'samsung']
['-PRON-', 'samsung', '-PRON-', 'living_room', 'know', 'quality', 'bought', 'small', '-PRON-', 'bedroom', 'set', '-PRON-', 'absolut